<a href="https://colab.research.google.com/github/dariakrtn/AI_2022/blob/main/lab_4_optuna.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# 0. *Импорт библиотек и вспомогательные функции/классы*

In [19]:
#!pip install optuna

In [20]:
import optuna
import sklearn.ensemble
import sklearn.svm
import logging

In [21]:
import logging
import sys

import sklearn.datasets
import sklearn.linear_model
import sklearn.model_selection
import optuna

In [22]:
from optuna.visualization import plot_contour
from optuna.visualization import plot_edf
from optuna.visualization import plot_intermediate_values
from optuna.visualization import plot_optimization_history
from optuna.visualization import plot_parallel_coordinate
from optuna.visualization import plot_param_importances
from optuna.visualization import plot_slice

# 1. *Применение оптуны на функцию Матьяса*

In [23]:
def f_mat (x, y):
  return 0.26*(x*x +y*y)-0.48*x*y

def objective(trial):
  x = trial.suggest_float('x', -10, 10)
  y = trial.suggest_float('y', -10, 10)
  return f_mat (x, y)

In [24]:
optuna.logging.disable_default_handler() 
optuna.logging.disable_propagation()
study =optuna.create_study()
study.optimize(objective, n_trials=100)


A new study created in memory with name: no-name-bcb3e81d-7f28-42fc-b7c1-8be55cdf922d
Trial 0 finished with value: 10.230091889514988 and parameters: {'x': -3.754713201804045, 'y': -9.570069919091775}. Best is trial 0 with value: 10.230091889514988.
Trial 1 finished with value: 3.7244140574270244 and parameters: {'x': -3.732999574285123, 'y': -6.947736198598513}. Best is trial 1 with value: 3.7244140574270244.
Trial 2 finished with value: 3.0239877987889408 and parameters: {'x': -8.718507252628012, 'y': -7.4263312791232705}. Best is trial 2 with value: 3.0239877987889408.
Trial 3 finished with value: 5.574498421542691 and parameters: {'x': 2.064055550223692, 'y': -2.656532604211166}. Best is trial 2 with value: 3.0239877987889408.
Trial 4 finished with value: 1.0578733046908635 and parameters: {'x': 3.7413880286292702, 'y': 4.867107867292296}. Best is trial 4 with value: 1.0578733046908635.
Trial 5 finished with value: 36.38954710474867 and parameters: {'x': 9.084225277518936, 'y': -2.

In [25]:
best_params = study.best_params
found_x = best_params['x']
found_y = best_params['y']
print(f"Found x: {found_x},  Found y: {found_y}, f_mat(x,y): {f_mat(found_x, found_y)}")

Found x: 0.1555362673554882,  Found y: 0.2069556047265202, f_mat(x,y): 0.0019749906371741965


# 2. *Использование datasets Iris и оптимизация параметров с помощью optuna*

In [26]:
def objective(trial):
    iris = sklearn.datasets.load_iris()  # грузим датасет
    classes = list(set(iris.target))
    train_x, valid_x, train_y, valid_y = sklearn.model_selection.train_test_split( # разюитие на тест и тренировку в данном случае 75 на 25
        iris.data, iris.target, test_size=0.25, random_state=0
    )


    max_iter = trial.suggest_int("max_iter", 50, 400)
    verbose = trial.suggest_int("verbose", 0, 100)
    clf = sklearn.linear_model.SGDClassifier(max_iter=max_iter, verbose = verbose)

    for step in range(100):
        clf.fit(train_x, train_y)

        # Report intermediate objective value.
        intermediate_value = 1.0 - clf.score(valid_x, valid_y)
        trial.report(intermediate_value, step)

        # Handle pruning based on the intermediate value.
        if trial.should_prune():
            raise optuna.TrialPruned()

    return 1.0 - clf.score(valid_x, valid_y)


In [27]:

optuna.logging.get_logger("optuna").addHandler(logging.StreamHandler(sys.stdout))
study = optuna.create_study(pruner=optuna.pruners.MedianPruner())
study.optimize(objective, n_trials=20)

Выходные данные были обрезаны до нескольких последних строк (5000).
-- Epoch 12
Norm: 329.35, NNZs: 4, Bias: -124.123466, T: 1344, Avg. loss: 12.828070
Total training time: 0.00 seconds.
-- Epoch 13
Norm: 326.11, NNZs: 4, Bias: -128.318744, T: 1456, Avg. loss: 12.825305
Total training time: 0.00 seconds.
-- Epoch 14
Norm: 316.84, NNZs: 4, Bias: -128.324951, T: 1568, Avg. loss: 5.893975
Total training time: 0.00 seconds.
-- Epoch 15
Norm: 314.38, NNZs: 4, Bias: -132.218397, T: 1680, Avg. loss: 11.241590
Total training time: 0.00 seconds.
-- Epoch 16
Norm: 312.73, NNZs: 4, Bias: -135.912314, T: 1792, Avg. loss: 6.760290
Total training time: 0.00 seconds.
-- Epoch 17
Norm: 303.91, NNZs: 4, Bias: -139.446078, T: 1904, Avg. loss: 4.140393
Total training time: 0.00 seconds.
-- Epoch 18
Norm: 294.25, NNZs: 4, Bias: -139.442735, T: 2016, Avg. loss: 0.782234
Total training time: 0.05 seconds.
-- Epoch 19
Norm: 291.35, NNZs: 4, Bias: -142.666753, T: 2128, Avg. loss: 5.834753
Total training time:

[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.0s finished
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.0s finished
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0


Total training time: 0.00 seconds.
-- Epoch 30
Norm: 157.44, NNZs: 4, Bias: 118.587734, T: 3360, Avg. loss: 21.292186
Total training time: 0.00 seconds.
-- Epoch 31
Norm: 155.66, NNZs: 4, Bias: 118.550007, T: 3472, Avg. loss: 25.618433
Total training time: 0.00 seconds.
-- Epoch 32
Norm: 155.90, NNZs: 4, Bias: 118.542178, T: 3584, Avg. loss: 17.352121
Total training time: 0.01 seconds.
-- Epoch 33
Norm: 150.48, NNZs: 4, Bias: 120.734550, T: 3696, Avg. loss: 27.818087
Total training time: 0.01 seconds.
-- Epoch 34
Norm: 140.66, NNZs: 4, Bias: 124.966381, T: 3808, Avg. loss: 21.789111
Total training time: 0.01 seconds.
-- Epoch 35
Norm: 146.66, NNZs: 4, Bias: 124.961407, T: 3920, Avg. loss: 24.878515
Total training time: 0.01 seconds.
-- Epoch 36
Norm: 145.43, NNZs: 4, Bias: 127.002497, T: 4032, Avg. loss: 26.157326
Total training time: 0.01 seconds.
-- Epoch 37
Norm: 144.40, NNZs: 4, Bias: 128.992531, T: 4144, Avg. loss: 20.560688
Total training time: 0.01 seconds.
Convergence after 37

[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.1s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.1s finished
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.1s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.1s finished
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s


Norm: 166.48, NNZs: 4, Bias: 117.001760, T: 2352, Avg. loss: 34.329471
Total training time: 0.08 seconds.
-- Epoch 22
Norm: 163.32, NNZs: 4, Bias: 119.860542, T: 2464, Avg. loss: 35.031374
Total training time: 0.08 seconds.
-- Epoch 23
Norm: 158.58, NNZs: 4, Bias: 122.653370, T: 2576, Avg. loss: 28.282897
Total training time: 0.08 seconds.
-- Epoch 24
Norm: 155.27, NNZs: 4, Bias: 122.616132, T: 2688, Avg. loss: 28.768127
Total training time: 0.08 seconds.
-- Epoch 25
Norm: 157.77, NNZs: 4, Bias: 122.652188, T: 2800, Avg. loss: 21.803769
Total training time: 0.08 seconds.
-- Epoch 26
Norm: 158.36, NNZs: 4, Bias: 125.290019, T: 2912, Avg. loss: 30.564479
Total training time: 0.08 seconds.
-- Epoch 27
Norm: 155.54, NNZs: 4, Bias: 127.831467, T: 3024, Avg. loss: 29.477419
Total training time: 0.08 seconds.
-- Epoch 28
Norm: 152.78, NNZs: 4, Bias: 132.741323, T: 3136, Avg. loss: 35.627483
Total training time: 0.08 seconds.
-- Epoch 29
Norm: 149.35, NNZs: 4, Bias: 135.134280, T: 3248, Avg. l

...

Total training time: 0.04 seconds.
-- Epoch 18
Norm: 273.56, NNZs: 4, Bias: -133.107197, T: 2016, Avg. loss: 4.424970
Total training time: 0.04 seconds.
-- Epoch 19
Norm: 273.18, NNZs: 4, Bias: -136.342951, T: 2128, Avg. loss: 8.138092
Total training time: 0.04 seconds.
-- Epoch 20
Norm: 270.10, NNZs: 4, Bias: -139.430930, T: 2240, Avg. loss: 3.466701
Total training time: 0.04 seconds.
-- Epoch 21
Norm: 267.15, NNZs: 4, Bias: -139.382474, T: 2352, Avg. loss: 6.402134
Total training time: 0.04 seconds.
Convergence after 21 epochs took 0.04 seconds
-- Epoch 1
Norm: 102.22, NNZs: 4, Bias: 9.901006, T: 112, Avg. loss: 11.152602
Total training time: 0.00 seconds.
-- Epoch 2
Norm: 92.86, NNZs: 4, Bias: 9.901006, T: 224, Avg. loss: 0.000000
Total training time: 0.00 seconds.
-- Epoch 3
Norm: 85.07, NNZs: 4, Bias: 9.901006, T: 336, Avg. loss: 0.000000
Total training time: 0.00 seconds.
-- Epoch 4
Norm: 78.48, NNZs: 4, Bias: 9.901006, T: 448, Avg. loss: 0.000000
Total training time: 0.00 second

[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.0s finished


Выходные данные были обрезаны до нескольких последних строк (5000).
Total training time: 0.02 seconds.
-- Epoch 10
Norm: 258.23, NNZs: 4, Bias: -84.644114, T: 1120, Avg. loss: 14.076483
Total training time: 0.02 seconds.
-- Epoch 11
Norm: 256.98, NNZs: 4, Bias: -89.235987, T: 1232, Avg. loss: 10.890191
Total training time: 0.02 seconds.
-- Epoch 12
Norm: 269.76, NNZs: 4, Bias: -93.603057, T: 1344, Avg. loss: 12.789710
Total training time: 0.02 seconds.
Convergence after 12 epochs took 0.02 seconds
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.0s finished
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
-- Epoch 1
Norm: 117.87, NNZs: 4, Bias: 9.892187, T: 112, Avg. loss: 14.453673
Total training time: 0.00 seconds.
-- Epoch 2
Norm: 107.08, NNZs: 4, Bias: 9.892187, T: 224, Avg. loss: 0.000000
Total training time: 0.00 seconds.
-- Epoch 3
Norm: 98.09, NNZs: 4, Bias: 

/usr/local/lib/python3.7/dist-packages/sklearn/linear_model/_stochastic_gradient.py:700: ConvergenceWarning:

Maximum number of iteration reached before convergence. Consider increasing max_iter to improve the fit.



Выходные данные были обрезаны до нескольких последних строк (5000).
-- Epoch 7
Norm: 57.07, NNZs: 4, Bias: 9.940633, T: 784, Avg. loss: 0.000000
Total training time: 0.00 seconds.
Convergence after 7 epochs took 0.00 seconds
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
-- Epoch 1
Norm: 82.35, NNZs: 4, Bias: 9.316107, T: 112, Avg. loss: 143.994275
Total training time: 0.00 seconds.
-- Epoch 2
Norm: 123.83, NNZs: 4, Bias: 26.368452, T: 224, Avg. loss: 106.126244
Total training time: 0.00 seconds.
-- Epoch 3
Norm: 145.77, NNZs: 4, Bias: 18.328662, T: 336, Avg. loss: 89.413032
Total training time: 0.00 seconds.
-- Epoch 4
Norm: 131.83, NNZs: 4, Bias: 39.798577, T: 448, Avg. loss: 104.165874
Total training time: 0.00 seconds.
-- Epoch 5
Norm: 131.85, NNZs: 4, Bias: 46.104329, T: 560, Avg. loss: 89.912034
Total training time: 0.00 seconds.
-- Epoch 6
Norm: 145.25, NNZs: 4, Bias: 58.436279, T: 672, Avg. loss: 73.131716
Total training time: 0.00 seconds.
-- E

In [28]:
plot_optimization_history(study)


In [29]:

plot_contour(study)


In [30]:
plot_parallel_coordinate(study)


In [31]:
plot_slice(study)


In [32]:
plot_param_importances(study)


In [33]:
plot_edf(study)